In [1]:
from helpers import load_data

In [2]:
data = load_data('wsmp_train.json')
eval_data = load_data('wsmp_dev.json')

In [3]:
data[0]

('ghaṭa stha yogam yoga īśa tattva jñānasya kāraṇam',
 [('ghaṭa', 'iic.'),
  ('stha', 'iic.'),
  ('yoga', 'm. sg. acc.'),
  ('yoga', 'iic.'),
  ('īśa', 'm. sg. voc.'),
  ('tattva', 'iic.'),
  ('jñāna', 'n. sg. g.'),
  ('kāraṇa', 'n. sg. acc.')])

In [34]:
token_stem_pairs = set()

for sentence, labels in data:
    tokens = sentence.split()
    stems, tags = zip(*labels)
    
    if len(tokens) != len(stems):
        continue
        
    for token, stem, tag in zip(tokens, stems, tags):
        token_stem_pairs.add((token, stem, tag))

token_stem_pairs = list(token_stem_pairs)

In [66]:
import numpy as np
from collections import defaultdict

rules = defaultdict(int)

"""
Find rules = operations how to transform token -> stem
"""

#for sentence, labels in data:
#    tokens = sentence.split()
#    stems, _ = zip(*labels)
    
    # Skip malformed data
#    if len(tokens) != len(stems):
#        continue
    
    # Find rule for each token, stem pair
#    for token, stem in zip(tokens, stems):
for token, stem, tag in token_stem_pairs:
    # Find possible starting indices for overlapping
    # sequences for chars
    (indices,) = np.nonzero([char == stem[0] for char in token])
    #for i, char in enumerate(token):
    #    if char == stem[0]:
    #        indices.append(i)
        
    # If no overlap, no rule
    if len(indices) == 0:
        continue
        
    # Find length of overlapping char segments
    match_lens = []
    for idx in indices:
        current_length = 0
        for k in range(0, min(len(stem), len(token) - idx)):
            if stem[k] == token[idx + k]:
                current_length += 1
            else:
                break
        match_lens.append(current_length)
        
    # Take longest overlapping char segment
    # as 'root' (may be different from linguistic root)
    best_idx = np.argmax(match_lens)
    best_length = match_lens[best_idx]
    best_idx = indices[best_idx]
        
    # If no overlap, no rule
    if best_length == 0:
        raise
        
    # Prefix = part before 'root'
    prefix = token[:best_idx]
    # Suffix = part after 'root'
    suffix = token[best_idx + best_length:]
    # Replaced suffix
    stem_suffix = stem[best_length:]
        
    # Save rule
    rules[(prefix, suffix, stem_suffix, tag)] += 1

In [67]:
len(rules)

3016

In [39]:
eval_token_stem_pairs = list()

for sentence, labels in eval_data:
    tokens = sentence.split()
    stems, tags = zip(*labels)
    
    if len(tokens) != len(stems):
        continue
        
    for token, stem, tag in zip(tokens, stems, tags):
        eval_token_stem_pairs.append((token, stem, tag))

#eval_token_stem_pairs = list(eval_token_stem_pairs)

In [40]:
len(eval_token_stem_pairs)

67927

In [76]:
from tqdm.notebook import tqdm

stem_success = 0
tag_success = 0
success = 0

valid_rules = [rule for rule, count in rules.items() if count > 5]
candidate_lengths = []

for token, stem, true_tag in tqdm(eval_token_stem_pairs):
    possible_stems = []
    possible_tags = []
    
    # Reconstruct candidates
    for prefix, suffix, stem_suffix, tag in valid_rules:
        possible_stem = token[:]
        if possible_stem.startswith(prefix):
            possible_stem = possible_stem[len(prefix):]
        else:
            continue
        
        if possible_stem.endswith(suffix):
            possible_stem = possible_stem[:len(possible_stem) - len(suffix)]
            possible_stem += stem_suffix
        else:
            continue
        
        possible_stems.append(possible_stem)
        possible_tags.append(tag)
    
    #possible_stems = list(sorted(set(possible_stems)))
    possible_stems = list(possible_stems)
    
    if stem in possible_stems:
        stem_success += 1
    if true_tag in possible_tags:
        tag_success += 1
    if true_tag in possible_tags and stem in possible_stems:
        success += 1
    
    candidate_lengths.append(len(possible_stems))

  0%|          | 0/67927 [00:00<?, ?it/s]

corau

0 5

corau

0 5

corau

0 5

cora
cora
1 5

corau

0 5

corau

0 5

corau

0 5

cora
cora
1 5

corau

0 5

corau

0 5

corau

0 5

cor
cor
2 5

corau

0 5

corau

0 5

cor
cor
2 5

corau

0 5

cor
cor
2 5

corau

0 5

cor
cor
2 5

corau

0 5

cor
cor
2 5

corau

0 5

corau

0 5

cor
cor
2 5

cora
cora
1 5

cor
cor
2 5

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāk
śvapāk
1 7

śvapāka

0 7

śvapāka

0 7

śvapāka

0 7

śvapāk
śvapāk
1 7

śvapāka

0 7

śvapāk
śvapāk
1 7

śvapāka

0 7

śvapāka

0 7

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍāla
caṇḍāla
1 8

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍāla
caṇḍāla
1 8

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍāl
caṇḍāl
2 8

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍāl
caṇḍāl
2 8

caṇḍālau

0 8

caṇḍāl
caṇḍāl
2 8

caṇḍālau

0 8

caṇḍāl
caṇḍāl
2 8

caṇḍālau

0 8

caṇḍāl
caṇḍāl
2 8

caṇḍālau

0 8

caṇḍālau

0 8

caṇḍāl
caṇḍāl


niśchidram

0 10

niśchidr
niśchidr
2 10

niśchidram

0 10

niśchidram

0 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇa
brāhmaṇa
2 10

brāhmaṇa
brāhmaṇa
2 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇaiḥ

0 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇaiḥ

0 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇ
brāhmaṇ
3 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇaiḥ

0 10

brāhmaṇai
brāhmaṇai
1 10

brāhmaṇaiḥ

0 10

upapāditam

0 10

upapādita
upapādita
1 10

upapāditam

0 10

upapāditam

0 10

upapādita
upapādita
1 10

upapādita
upapādita
1 10

upapādit
upapādit
2 10

upapādita
upapādita
1 10

upapāditam

0 10

upapādit
upapādit
2 10

upapāditam

0 10

upapāditam

0 10

upapāditam

0 10

upapāditam

0 10

upapādit

3 8

vipr
vipr
4 8

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣ
brahmaghoṣ
3 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣ
brahmaghoṣ
3 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇ
brahmaghoṣeṇ
1 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇ
brahmaghoṣeṇ
1 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇ
brahmaghoṣeṇ
1 13

brahmaghoṣeṇa

0 13

brahmaghoṣeṇa

0 13

bhojyam

0 7

bhojya
bhojya
1 7

bhojyam

0 7

bhojyam

0 7

bhojya
bhojya
1 7

bhojya
bhojya
1 7

bhojy
bhojy
2 7

bhojya
bhojya
1 7

bhojyam

0 7

bhojy
bhojy
2 7

bhojyam

0 7

bhojyam

0 7

bhojyam

0 7

bhojyam

0 7

bhojyam

0 7

bhojyam

0 7

bhojy
bhojy
2 7

bhojyam

0 7

bhojy
bhojy
2 7

bhojyam

0 7

bhojyam

0 7

bhojyam

0 7

bhojy
bhojy
2 7

bhojyam

0 7

bhojyam

0 7

bhavati

0 7

bhavati

0 7

bhavati

0 7

bhavat
bhavat
1 7

bhavat
bhavat
1 7

bhava
bhava
2 7

bhavati

0

vā

0 2

vā

0 2

vā

0 2

v
v
1 2

vā

0 2



2 2

śakaṭe

0 6

śakaṭ
śakaṭ
1 6

śakaṭe

0 6

śakaṭ
śakaṭ
1 6

śakaṭe

0 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭ
śakaṭ
1 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭe

0 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭe

0 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

śakaṭe

0 6

śakaṭ
śakaṭ
1 6

śakaṭ
śakaṭ
1 6

paṅktau

0 7

paṅktau

0 7

paṅktau

0 7

paṅkta
paṅkta
1 7

paṅktau

0 7

paṅktau

0 7

paṅktau

0 7

paṅkta
paṅkta
1 7

paṅktau

0 7

paṅktau

0 7

paṅktau

0 7

paṅkt
paṅkt
2 7

paṅktau

0 7

paṅktau

0 7

paṅkt
paṅkt
2 7

paṅktau

0 7

paṅkt
paṅkt
2 7

paṅktau

0 7

paṅkt
paṅkt
2 7

paṅktau

0 7

paṅkt
paṅkt
2 7

paṅktau

0 7

paṅktau

0 7

paṅkt
paṅkt
2 7

paṅkta
paṅkta
1 7

paṅkt
paṅkt
2 7

pṛṣṭhe

0 6

pṛṣṭh
pṛṣṭh
1 6

pṛṣṭhe

0 6

pṛṣṭh
pṛ

...

prāṇeśvar
2 11

prāṇeśvara
prāṇeśvara
1 11

prāṇeśvaram

0 11

prāṇeśvar
prāṇeśvar
2 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

prāṇeśvar
prāṇeśvar
2 11

prāṇeśvaram

0 11

prāṇeśvar
prāṇeśvar
2 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

prāṇeśvar
prāṇeśvar
2 11

prāṇeśvaram

0 11

prāṇeśvaram

0 11

śambhum

0 7

śambhu
śambhu
1 7

śambhum

0 7

śambhum

0 7

śambhu
śambhu
1 7

śambhu
śambhu
1 7

śambhu
śambhu
1 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

śambhum

0 7

asau

0 4

asau

0 4

asau

0 4

asa
asa
1 4

asau

0 4

asau

0 4

asau

0 4

asa
asa
1 4

asau

0 4

asau

0 4

asau

0 4

as
as
2 4

asau

0 4

asau

0 4

as
as
2 4

asau

0 4

as
as
2 4

asau

0 4

as
as
2 4

asau

0 4

as
as
2 4

asau

0 4

asau

0 4

as
as
2 4

asa
asa
1 4

as
as
2 4

dadarśa

0 7


tatra

0 5

tatra

0 5

tatra

0 5

tatra

0 5

tatra

0 5

tatra

0 5

tatra

0 5

tatra

0 5

tatra

0 5

tatra

0 5

tatr
tatr
1 5

tatra

0 5

tatra

0 5

tatra

0 5

tatr
tatr
1 5

tatra

0 5

tatr
tatr
1 5

tatra

0 5

tatra

0 5

nivāsina
nivāsina
1 9

nivāsina
nivāsina
1 9

nivāsinaḥ

0 9

nivāsinaḥ

0 9

nivāsin
nivāsin
2 9

nivāsinaḥ

0 9

nivāsin
nivāsin
2 9

nivāsin
nivāsin
2 9

nivāsin
nivāsin
2 9

nivāsina
nivāsina
1 9

nivāsin
nivāsin
2 9

nivāsinaḥ

0 9

nivāsinaḥ

0 9

nivāsina
nivāsina
1 9

nivāsinaḥ

0 9

nivāsinaḥ

0 9

nivāsinaḥ

0 9

nivāsin
nivāsin
2 9

nivāsina
nivāsina
1 9

nivāsina
nivāsina
1 9

nivāsinaḥ

0 9

nivāsin
nivāsin
2 9

nivāsina
nivāsina
1 9

nivāsinaḥ

0 9

nivāsina
nivāsina
1 9

nivāsin
nivāsin
2 9

nivāsi
nivāsi
3 9

nivāsinaḥ

0 9

nivāsinaḥ

0 9

nivāsina
nivāsina
1 9

nivāsinaḥ

0 9

nivāsin
nivāsin
2 9

nivāsinaḥ

0 9

nivāsinaḥ

0 9

nivāsin
nivāsin
2 9

nivāsina
nivāsina
1 9

nivāsinaḥ

0 9

nivāsin
nivāsin
2 9

gate

0 4

gat
gat
1 4

gat


vai

0 3

va
va
1 3

va
va
1 3

paśyanti

0 8

paśyanti

0 8

paśyanti

0 8

paśyant
paśyant
1 8

paśyant
paśyant
1 8

paśyan
paśyan
2 8

paśyanti

0 8

paśyanti

0 8

paśyanti

0 8

paśyanti

0 8

paśyanti

0 8

paś
paś
5 8

paśyanti

0 8

paśyanti

0 8

paśyanti

0 8

paśy
paśy
4 8

paśyanti

0 8

paśyant
paśyant
1 8

paśyanti

0 8

paśy
paśy
4 8

paśyanti

0 8

paśyanti

0 8

paśya
paśya
3 8

paśyant
paśyant
1 8

paśy
paśy
4 8

paśya
paśya
3 8

paśyanti

0 8

paśy
paśy
4 8

paśya
paśya
3 8

paśyant
paśyant
1 8

paśyant
paśyant
1 8

tam

0 3

ta
ta
1 3

tam

0 3

tam

0 3

ta
ta
1 3

ta
ta
1 3

t
t
2 3

ta
ta
1 3

tam

0 3

t
t
2 3

tam

0 3

tam

0 3

tam

0 3

tam

0 3

tam

0 3

tam

0 3

t
t
2 3

tam

0 3

t
t
2 3

tam

0 3

tam

0 3

tam

0 3

t
t
2 3

tam

0 3

tam

0 3

devam

0 5

deva
deva
1 5

devam

0 5

devam

0 5

deva
deva
1 5

deva
deva
1 5

dev
dev
2 5

deva
deva
1 5

devam

0 5

dev
dev
2 5

devam

0 5

devam

0 5

devam

0 5

devam

0 5

devam

0 5

devam

0 5

dev


śūlina
śūlina
1 7

śūlinaḥ

0 7

śūlin
śūlin
2 7

māyayā

0 6

māyayā

0 6

māyayā

0 6

māyay
māyay
1 6

māyay
māyay
1 6

māyay
māyay
1 6

māyay
māyay
1 6

māya
māya
2 6

māyay
māyay
1 6

māyayā

0 6

māyayā

0 6

māyayā

0 6

māyay
māyay
1 6

māyayā

0 6

māyayā

0 6

māy
māy
3 6

māyayā

0 6

māyayā

0 6

māya
māya
2 6

māyayā

0 6

māyayā

0 6

māyayā

0 6

māyayā

0 6

māya
māya
2 6

māyayā

0 6

māyay
māyay
1 6

māya
māya
2 6

māyayā

0 6

mohitau

0 7

mohitau

0 7

mohitau

0 7

mohita
mohita
1 7

mohitau

0 7

mohitau

0 7

mohitau

0 7

mohita
mohita
1 7

mohitau

0 7

mohitau

0 7

mohitau

0 7

mohit
mohit
2 7

mohitau

0 7

mohitau

0 7

mohit
mohit
2 7

mohitau

0 7

mohit
mohit
2 7

mohitau

0 7

mohit
mohit
2 7

mohitau

0 7

mohit
mohit
2 7

mohitau

0 7

mohitau

0 7

mohit
mohit
2 7

mohita
mohita
1 7

mohit
mohit
2 7

tasya

0 5

tasya

0 5

ta
ta
3 5

tasya

0 5

ta
ta
3 5

tasya

0 5

tasya

0 5

tasya

0 5

tasya

0 5

tasya

0 5

tasya

0 5

tasya

0 5

tasy
ta

KeyboardInterrupt: 

In [73]:
print(f"Perc. of reconstructed stems: {stem_success / len(eval_token_stem_pairs)}")
print(f"Perc. of reconstructed tags: {tag_success / len(eval_token_stem_pairs)}")
print(f"Perc. of both reconstructed: {success / len(eval_token_stem_pairs)}")
print(f"Avg. number of candidate stems: {np.mean(candidate_lengths)}")

Perc. of reconstructed stems: 0.5461156830126459
Perc. of reconstructed tags: 0.9667731535324687
Perc. of both reconstructed: 0.5426413649947738
Avg. number of candidate stems: 25.719154386326498


In [74]:
possible_stems

['',
 '',
 '',
 'nyadadha',
 'nyadadha',
 '',
 '',
 '',
 '',
 '',
 'n',
 'n',
 '',
 'nyadadhād',
 '',
 'nyadadhād',
 '',
 '',
 'nyadadhād',
 'n',
 '']

In [47]:
stem

'nidhā'

In [53]:
len(valid_rules)

472

In [77]:
valid_rules[-20:]

[('', 'dbhyaḥ', 't', 'm. pl. dat.'),
 ('', 'u', '', 'm. du. voc.'),
 ('', 'yoḥ', 'i', 'm. du. g.'),
 ('', 'yante', 'ay', 'ca. pr. ps. pl. 3'),
 ('', 'vā', 'u', 'f. sg. i.'),
 ('', 'ṣaḥ', 's', 'n. sg. abl.'),
 ('', 'ati', '', 'pr. [10] ac. sg. 3'),
 ('', 'yataḥ', '', 'pr. [4] ac. du. 3'),
 ('', 'syasi', '', 'fut. ac. sg. 2'),
 ('', 'ñjīta', 'j', 'opt. [7] md. sg. 3'),
 ('', 'smai', '', 'm. sg. dat.'),
 ('', 'āni', 'an', 'n. pl. nom.'),
 ('', 'au', '', 'm. du. acc.'),
 ('', 'ṇaḥ', 'n', 'n. sg. g.'),
 ('', 'bhyaḥ', 'n', 'm. pl. abl.'),
 ('', 'yaḥ', 'i', 'f. pl. nom.'),
 ('', 'atām', '', 'imp. [1] md. sg. 3'),
 ('', 'avaḥ', 'u', 'f. pl. nom.'),
 ('', 'at', '', 'ca. impft. ac. sg. 3'),
 ('', 'ūṇi', 'u', 'n. pl. nom.')]

In [78]:
len(set([tag for _, _, _, tag in valid_rules]))

169

In [56]:
set([prefix for prefix, _, _, _ in valid_rules])

{'', 'a', 'ja'}